In [1]:
## %matplotlib inline
%matplotlib osx
import matplotlib.pyplot as plt
import numpy as np
import json
import requests
import matplotlib as mpl
import matplotlib.pyplot as plt
from nba_api.stats.static import players 
from nba_api.stats.static import teams
from nba_api.stats.endpoints import shotchartdetail
import pandas as pd
import time
from matplotlib.animation import FFMpegWriter

# (1) Set up for making a request to the nba api

In [2]:
# Storing Directory for All Players
player_dict = players.get_players()
team_dict   = teams.get_teams()
# print(team_dict)
print(team_dict[0])

{'id': 1610612737, 'full_name': 'Atlanta Hawks', 'abbreviation': 'ATL', 'nickname': 'Hawks', 'city': 'Atlanta', 'state': 'Atlanta', 'year_founded': 1949}


In [3]:
def get_player(first_name, last_name):
    for player in player_dict:
        if first_name == player['first_name'] and last_name == player['last_name']:
            print('found player: ', player['full_name'])
            return player
    return None    

def get_player_id(first_name, last_name):
    player = get_player(first_name, last_name)
    
    if player == None:
        return -1
    return player['id']

In [4]:
get_player_id("LeBron", "James")

found player:  LeBron James


2544

In [5]:
def get_team_by_abv(abv):
    for team in team_dict:
        if team['abbreviation'] == abv:
            return team
    return None

def get_team_id_by_abv(abv):
    team = get_team_by_abv(abv)
    if team == None:
        return -1
    return team['id']



In [6]:
def get_team_by_name(full_name):
    for team in team_dict:
        if team['full_name'] == full_name:
            return team
    return None
    
def get_team_id_by_name(abv):
    team = get_team_by_name(abv)
    if team == None:
        return -1
    return team['id']

In [7]:
print("team: ", get_team_by_name('Los Angeles Lakers'))
print("id: ", get_team_id_by_abv('LAL'))
print("id: ", get_team_id_by_name('Atlanta Hawks'))

team:  {'id': 1610612747, 'full_name': 'Los Angeles Lakers', 'abbreviation': 'LAL', 'nickname': 'Lakers', 'city': 'Los Angeles', 'state': 'California', 'year_founded': 1948}
id:  1610612747
id:  1610612737


In [8]:
""" Calls the nba api to get SHOT_JSON for a players based on TEAM_ABV, PLAYER_*, CTX, SEASON, and SEASON_TYPE
    Then extracts the columns HEADERS corresponding to the data of the SHOT_RESULTS of a player, puts them into a pandas
    table, and fills out the ROWS of the pandas table with ROWS.
    
    Returns None if the player did (or has if season was too late) not play in that year, or just an invalid input
    otherwise returns back the pandas table
    
    If PLAYER_* == "", returns a table corresponding to the whole team for that season.
"""
def generate_shot_data(team_abv, player_first_name, player_last_name, ctx, season, season_type):
    
    # Get team id and player id, check to make sure the player exists. 
    team_id = get_team_id_by_abv(team_abv),
    if player_first_name == "" and player_last_name == "":
        player_id = 0
    else:
        player_id = get_player_id(player_first_name, player_last_name),
    
    if team_id == None or player_id == -1:
        return None
    
    shot_json = shotchartdetail.ShotChartDetail(
                team_id = team_id,
                player_id = player_id,
                context_measure_simple = ctx,
                season_nullable = season,
                season_type_all_star = season_type)
    
    
    shot_data    = json.loads(shot_json.get_json())
    shot_results = shot_data['resultSets'][0]
    
    headers = shot_results['headers']
    rows    = shot_results['rowSet']
    
    if (len(rows) == 0):
        return pd.DataFrame()
    player_data = pd.DataFrame(rows)
    player_data.columns = headers
    
    # print('Finished making the api request')
    return player_data

# player_data = generate_shot_data('LAL', 'LeBron', 'James', 'PTS', '2021-22', 'Regular Season')
# print(player_data)

# (2) Make the basketball court

In [9]:
# Function to draw basketball court
def create_court(ax, color):
    # Short corner 3PT lines
    ax.plot([-220, -220], [0, 140], linewidth=2, color=color)
    ax.plot([220, 220], [0, 140], linewidth=2, color=color)
    
    # 3PT Arc
    ax.add_artist(mpl.patches.Arc((0, 140), 440, 315, theta1=0, theta2=180, facecolor='none', edgecolor=color, lw=2))
    
    # Lane and Key
    ax.plot([-80, -80], [0, 190], linewidth=2, color=color)
    ax.plot([80, 80], [0, 190], linewidth=2, color=color)
    ax.plot([-60, -60], [0, 190], linewidth=2, color=color)
    ax.plot([60, 60], [0, 190], linewidth=2, color=color)
    ax.plot([-80, 80], [190, 190], linewidth=2, color=color)
    ax.add_artist(mpl.patches.Circle((0, 190), 60, facecolor='none', edgecolor=color, lw=2))
    
    # Rim
    ax.add_artist(mpl.patches.Circle((0, 60), 15, facecolor='none', edgecolor=color, lw=2))
    
    # Backboard
    ax.plot([-30, 30], [40, 40], linewidth=2, color=color)
    
    # Remove ticks
    ax.set_xticks([])
    ax.set_yticks([])
        
    # Set axis limits
    ax.set_xlim(-250, 250)
    ax.set_ylim(0, 470)
    

In [10]:
# First, plots points of made shots based on PLAYER_DATA, then prints out the court
def generate_plot(fig, ax, player_data, player_first_name, player_last_name, team_abv, ctx, season, season_type):
    
    # General plot parameters
    mpl.rcParams['font.family'] = 'Avenir'
    mpl.rcParams['font.size'] = 16
    mpl.rcParams['axes.linewidth'] = 2
    
    # fig = plt.figure(figsize=(4, 3.76))
    # ax = fig.add_axes([0, 0, 1, 1])
    
    # ax_hexbin_C = [ player_data['GAME_EVENT_ID'] for made_flag in player_data['SHOT_MADE_FLAG'] if made_flag == 1]
    ax_hexbin_C = player_data.loc[player_data['SHOT_MADE_FLAG'] == 1]
    ax_hexbin_D = player_data.loc[player_data['SHOT_MADE_FLAG'] == 0]
    
    # Plot hexbin of shots with logarithmic binning
    # ax.hexbin(ax_hexbin_D['LOC_X'], ax_hexbin_D['LOC_Y'] + 60, gridsize=(30, 30), extent=(-300, 300, 0, 940), bins='log', cmap='Reds')
    ax.hexbin(ax_hexbin_C['LOC_X'], ax_hexbin_C['LOC_Y'] + 60, gridsize=(30, 30), extent=(-300, 300, 0, 940), bins='log', cmap='Blues')
    
    # Annotate player name and season
    annotation = team_abv + ' ' + player_first_name + ' ' + player_last_name + '\n' + season + ' ' + season_type + ' ' + ctx
    
    create_court(ax, 'black')
    ax.text(.01, .85, annotation, transform=ax.transAxes, ha='left', va='baseline')
    
    plt.show()
    
    return ax, fig
    
# fig = plt.figure(figsize=(4, 3.76))
# ax = fig.add_axes([0, 0, 1, 1])
# player_data = generate_shot_data('LAL', 'LeBron', 'James', 'FGA', '2021-22', 'Regular Season')
# generate_plot(fig, ax, player_data, "LeBron", "James", 'LAL', 'FGA', '2021-22', "Regular Season")


In [11]:
def year_to_season(year):
    next_year = year + 1
    
    year_str = str(year)
    next_year_str = str(next_year)
    
    out = year_str + "-" + next_year_str[2:]
    return out


# (3) Main functionality

In [12]:
def main_player(team_abv, player_first_name, player_last_name, ctx, season, season_type):
    player_data = generate_shot_data(team_abv, player_first_name, player_last_name, ctx, season, season_type)
    if player_data.empty:
        return -1
    
    fig = plt.figure(figsize=(4, 3.76))
    ax = fig.add_axes([0, 0, 1, 1])
    generate_plot(fig, ax, player_data, player_first_name, player_last_name, team_abv, ctx, season, season_type)
    
    # To see if a shot is a miss or a make w/ the SHOT_MADE_FLAG if we are using a fga
    print(player_data['SHOT_MADE_FLAG'])
    return 0
    

In [13]:
# main_player('LAL', 'LeBron', 'James', 'PTS', '2021-22', 'Regular Season')
# main('GSW', '', '', 'PTS', '2021-22', 'Regular Season')
# main_player('GSW', '', '', 'FGA', year_to_season(2021), 'Regular Season')
# main_player('GSW', '', '', 'PTS', year_to_season(2021), 'Regular Season')

In [14]:
class nba_api_args:
    def __init__(self, team_abv, player_first_name, player_last_name, ctx, start_season, end_season, season_type):
        self.team_abv     = team_abv
        self.first_name   = player_first_name
        self.last_name    = player_last_name
        self.ctx          = ctx
        self.start_season = start_season
        self.end_season   = end_season
        self.season_num   = end_season
        self.season_type  = season_type
        # self.fig = plt.figure(figsize=(4, 3.76))
        # self.ax = fig.add_axes([0, 0, 1, 1])
        
    def generate_data(self, season):
        if season < self.start_season or season > self.end_season:
            return None
        
        season = year_to_season(season)
        data = generate_shot_data(self.team_abv, self.first_name, self.last_name, self.ctx, season, self.season_type) 
        return data
    
    def generate_plot(self, fig, ax, data, season):
        # print(data)
        generate_plot(fig, ax, data, self.first_name, self.last_name, self.team_abv, self.ctx, year_to_season(season), self.season_type)
        
    def main(self, fig, season):
        # print('attempting to generate data')
        # fig = plt.figure(figsize=(4, 3.76))
        ax = fig.add_axes([0, 0, 1, 1])
        
        data = self.generate_data(season)
        if (data.empty):
            print('failed to generate the data')
            return -1
        return self.generate_plot(fig, ax, data, season)
    
    def main_loop(self):
        out = 0
        while self.season_num > self.start_season and out != -1:
            fig = plt.figure(figsize=(4, 3.76))
            out = self.main(fig, self.season_num)
            self.season_num -= 1
            print("season_num: ", self.season_num)
            time.sleep(.5)
            # fig.close()
        self.season_num = self.end_season
        
    def main_loop_record(self):
        metadata = dict(title='Recording a players data', artist='Matplotlib',comment='')
        writer = FFMpegWriter(fps=2, metadata=metadata)
        fig = plt.figure(figsize=(4, 3.76))
        
        output_file_name = "results/"
        if (self.first_name != '' and self.last_name != ''):
            output_file_name += self.team_abv + '-' + self.first_name + '-' + self.last_name + '-' + 'shot-data.mp4'
        else:
            output_file_name += self.team_abv + '-shot-data.mp4'
        with writer.saving(fig, output_file_name, dpi=200):
            # nf = 100
            out = 0
            while self.season_num > self.start_season:
                    plt.clf()
                    out = self.main(fig, self.season_num)
                    if out == -1:
                        break
                    self.season_num -= 1
                    # print("season_num: ", self.season_num)
                    plt.show()
                    plt.draw()
                    plt.pause(.5)
                    writer.grab_frame()
        
    

In [15]:
gsw_team = get_team_by_abv('GSW')
gsw_start_season = gsw_team['year_founded']
gsw_fga = nba_api_args(
    team_abv='GSW',
    player_first_name='',
    player_last_name='',
    ctx='FGM',
    start_season=get_team_by_abv('GSW')['year_founded'],
    end_season=2022,
    season_type='Regular Season'
)

# gsw_fga.main(gsw_fga.end_season)
# gsw_fga.main(1964)

# gsw_fga.main_loop()

# gsw_fga.main_loop_record()


# (4) Create videos for all teams

In [17]:
all_team_abv = [team['abbreviation'] for team in team_dict]
print(all_team_abv, len(all_team_abv))

for abv in all_team_abv:
    # print('running ', abv)
    team_fga = nba_api_args(
        team_abv=abv,
        player_first_name='',
        player_last_name='',
        ctx='FGM',
        start_season=get_team_by_abv(abv)['year_founded'],
        end_season=2022,
        season_type='Regular Season'
    )
    # team_fga.main_loop_record()


# gsw_fga.main_loop()
# gsw_fga.main_loop_record()



['ATL', 'BOS', 'CLE', 'NOP', 'CHI', 'DAL', 'DEN', 'GSW', 'HOU', 'LAC', 'LAL', 'MIA', 'MIL', 'MIN', 'BKN', 'NYK', 'ORL', 'IND', 'PHI', 'PHX', 'POR', 'SAC', 'SAS', 'OKC', 'TOR', 'UTA', 'MEM', 'WAS', 'DET', 'CHA'] 30


In [25]:
presentation_teams = ['GSW', 'LAL', 'BOS']

In [26]:
metadata = dict(title='Recording a players data', artist='Matplotlib',comment='')
writer = FFMpegWriter(fps=2, metadata=metadata)
fig = plt.figure(figsize=(4, 3.76))

output_file_name = "presentation_result_data.mp4"
with writer.saving(fig, output_file_name, dpi=200):
    # nf = 100
    out = 0
    for abv in presentation_teams:
        print('running ', abv)
        team_fga = nba_api_args(
            team_abv=abv,
            player_first_name='',
            player_last_name='',
            ctx='FGM',
            start_season=get_team_by_abv(abv)['year_founded'],
            end_season=2022,
            season_type='Regular Season'
        )
        while out != -1:
            plt.clf()
            out = team_fga.main(fig, team_fga.season_num)
            team_fga.season_num -= 1
            # print("season_num: ", self.season_num)
            plt.show()
            plt.draw()
            plt.pause(.5)
            writer.grab_frame()
        out = 0



running  GSW
failed to generate the data
running  LAL
failed to generate the data
running  BOS
failed to generate the data
